# **Bitcoin price forecasting - GBTRegressor**
### Big Data Computing final project - A.Y. 2022 - 2023
Prof. Gabriele Tolomei

MSc in Computer Science

La Sapienza, University of Rome

### Author
Corsi Danilo - corsi.1742375@studenti.uniroma1.it



## Global constants, dependencies, libraries and tools

In [1]:
# GDrive root
GDRIVE_DIR = "/content/drive"

# Dataset
GDRIVE_DATASET_OUTPUT_DIR = GDRIVE_DIR + "/MyDrive/BDC/project/datasets/output"
GDRIVE_DATASET_NAME = "bitcoin_blockchain_data_30min"
GDRIVE_DATASET_NAME_ENG = GDRIVE_DATASET_NAME + "_train_valid"
GDRIVE_DATASET_NAME_EXT_ENG  = "/" + GDRIVE_DATASET_NAME_ENG + ".parquet"
GDRIVE_DATASET_NAME_ENG = GDRIVE_DATASET_OUTPUT_DIR + GDRIVE_DATASET_NAME_EXT_ENG

# Features
GDRIVE_FEATURES_DIR = GDRIVE_DIR + "/MyDrive/BDC/project/features"
GDRIVE_ALL_FEATURES_NAME = "all_features"
GDRIVE_MORE_REL_FEATURES_NAME = "more_rel_features"
GDRIVE_LESS_REL_FEATURES_NAME = "less_rel_features"
GDRIVE_ALL_FEATURES_NAME_EXT = "/" + GDRIVE_ALL_FEATURES_NAME + ".json"
GDRIVE_MORE_REL_FEATURES_NAME_EXT = "/" + GDRIVE_MORE_REL_FEATURES_NAME + ".json"
GDRIVE_LESS_REL_FEATURES_NAME_EXT = "/" + GDRIVE_LESS_REL_FEATURES_NAME + ".json"
GDRIVE_ALL_FEATURES = GDRIVE_FEATURES_DIR + GDRIVE_ALL_FEATURES_NAME_EXT
GDRIVE_MORE_REL_FEATURES = GDRIVE_FEATURES_DIR + GDRIVE_MORE_REL_FEATURES_NAME_EXT
GDRIVE_LESS_REL_FEATURES = GDRIVE_FEATURES_DIR + GDRIVE_LESS_REL_FEATURES_NAME_EXT

# Others
JAVA_HOME = "/usr/lib/jvm/java-8-openjdk-amd64"
MODEL_NAME = "GBTRegressor"
SLOW_OPERATION = True

In [2]:
# Point Colaboratory to our Google Drive
from google.colab import drive

# Define GDrive paths
drive.mount(GDRIVE_DIR, force_remount=True)

Mounted at /content/drive


In [3]:
import warnings

warnings.simplefilter(action='ignore', category=FutureWarning)

In [4]:
# Install Spark and related dependencies
!pip install pyspark

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 310.8/310.8 MB 4.5 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
  Created wheel for pyspark: filename=pyspark-3.4.1-py2.py3-none-any.whl size=311285388 sha256=a7d4db54b86d9b3d6e0e4bb110056bd5386dc24d3c19fe12d7c0af2106133297
  Stored in directory: /root/.cache/pip/wheels/0d/77/a3/ff2f74cc9ab41f8f594dabf0579c2a7c6de920d584206e0834
Successfully built pyspark


## Import files

In [5]:
GDRIVE_UTILITIES_DIR = GDRIVE_DIR + "/MyDrive/BDC/project/utilities"

import sys
sys.path.append(GDRIVE_UTILITIES_DIR)

from imports import *
import utilities, parameters

importlib.reload(utilities)
importlib.reload(parameters)

<module 'parameters' from '/content/drive/MyDrive/BDC/project/utilities/parameters.py'>

## Create the pyspark session

In [6]:
# Create the session
conf = SparkConf().\
                set('spark.ui.port', "4050").\
                set('spark.executor.memory', '4G').\
                set('spark.driver.memory', '45G').\
                set('spark.driver.maxResultSize', '10G').\
                set("spark.kryoserializer.buffer.max", "1G").\
                setAppName("BitcoinPriceForecasting").\
                setMaster("local[*]")

# Create the context
sc = pyspark.SparkContext(conf=conf)
spark = SparkSession.builder.getOrCreate()

## Loading dataset

In [7]:
# Load datasets into pyspark dataset objects
df = spark.read.load(GDRIVE_DATASET_NAME_ENG,
                         format="parquet",
                         sep=",",
                         inferSchema="true",
                         header="true"
                    )

In [8]:
def dataset_info(dataset):
  dataset.show(3)

  # Get the number of rows
  num_rows = dataset.count()

  # Get the number of columns
  num_columns = len(dataset.columns)

  # Print the shape of the dataset
  print("Shape:", (num_rows, num_columns))

  # Print the schema of the dataset
  dataset.printSchema()

In [9]:
if SLOW_OPERATION:
  dataset_info(df)

+-------------------+---+------------------+--------------+-------------------+--------------+------------------+------------------+--------------------+------------------------+-----------------+-------------------+------------------+--------------------+------------------+------------------+--------------------------------+--------------------+------------------+------------------+------------------+------------------+------------------+------------------+
|          timestamp| id|      market-price|total-bitcoins|         market-cap|  trade-volume|       blocks-size|    avg-block-size|n-transactions-total|n-transactions-per-block|        hash-rate|         difficulty|    miners-revenue|transaction-fees-usd|n-unique-addresses|    n-transactions|estimated-transaction-volume-usd|      rate-of-change|        sma-5-days|        sma-7-days|       sma-10-days|       sma-20-days|       sma-50-days|      sma-100-days|
+-------------------+---+------------------+--------------+---------------

## [TO DELETE] ADDING NEXT-MARKET-PRICE ❗

In [10]:
# # Add the column 'tomorrow-market-price' which will be the target feature on which to make predictions
# df = df.withColumn("next-market-price", F.lag("market-price", offset=-1) \
#         .over(Window.orderBy("id"))) \
#         .dropna()

# if SLOW_OPERATION:
#   dataset_info(df)

+-------------------+---+------------------+--------------+-------------------+--------------+------------------+------------------+--------------------+------------------------+-----------------+-------------------+------------------+--------------------+------------------+------------------+--------------------------------+--------------------+------------------+------------------+------------------+------------------+------------------+------------------+------------------+
|          timestamp| id|      market-price|total-bitcoins|         market-cap|  trade-volume|       blocks-size|    avg-block-size|n-transactions-total|n-transactions-per-block|        hash-rate|         difficulty|    miners-revenue|transaction-fees-usd|n-unique-addresses|    n-transactions|estimated-transaction-volume-usd|      rate-of-change|        sma-5-days|        sma-7-days|       sma-10-days|       sma-20-days|       sma-50-days|      sma-100-days| next-market-price|
+-------------------+---+-----------

## Loading features

In [11]:
# Set the features label
FEATURES_LABEL = "features"

# Set the target variable
TARGET_VAL = 'next-market-price'

In [12]:
# Loading correlation matrix features
with open(GDRIVE_ALL_FEATURES, "r") as f:
    all_features = json.load(f)
print(all_features)

['market-price', 'total-bitcoins', 'market-cap', 'trade-volume', 'blocks-size', 'avg-block-size', 'n-transactions-total', 'n-transactions-per-block', 'hash-rate', 'difficulty', 'miners-revenue', 'transaction-fees-usd', 'n-unique-addresses', 'n-transactions', 'estimated-transaction-volume-usd', 'rate-of-change', 'sma-5-days', 'sma-7-days', 'sma-10-days', 'sma-20-days', 'sma-50-days', 'sma-100-days']


In [13]:
# Loading correlation matrix features
with open(GDRIVE_MORE_REL_FEATURES, "r") as f:
    more_rel_features = json.load(f)
print(more_rel_features)

['market-price', 'market-cap', 'miners-revenue', 'sma-5-days', 'sma-7-days', 'estimated-transaction-volume-usd', 'sma-10-days', 'n-transactions-total', 'blocks-size', 'sma-100-days', 'total-bitcoins']


In [14]:
# Loading correlation matrix features
with open(GDRIVE_LESS_REL_FEATURES, "r") as f:
    less_rel_features = json.load(f)
print(less_rel_features)

['sma-50-days', 'sma-20-days', 'difficulty', 'hash-rate', 'n-unique-addresses', 'avg-block-size', 'transaction-fees-usd', 'trade-volume', 'n-transactions-per-block', 'n-transactions', 'rate-of-change']


## Simple model

In [15]:
# Get default params
params = parameters.get_defaults_model_params(MODEL_NAME)
params

{'maxIter': [20], 'maxDepth': [5], 'stepSize': [0.1]}

In [16]:
# Valid performances with all the features
simple_res_all, simple_pred_all = utilities.evaluate_simple_model(df, all_features, params, GDRIVE_ALL_FEATURES_NAME, MODEL_NAME, FEATURES_LABEL, TARGET_VAL, False)
simple_res_all

Model    Type      Features    Parameters         RMSE      MAPE  \
0  GBTRegressor  simple  all_features  [20, 5, 0.1]  2143.429339  0.067424   

           MAE      Variance        R2  Adjusted_R2       Time  
0  1516.468454  5.544397e+06  0.498092     0.497894  29.956248

In [17]:
utilities.show_results(simple_pred_all, MODEL_NAME, TARGET_VAL)

In [18]:
# Valid performances with the corr matrix features
simple_res_more_rel, simple_pred_more_rel = utilities.evaluate_simple_model(df, more_rel_features, params, GDRIVE_MORE_REL_FEATURES_NAME, MODEL_NAME, FEATURES_LABEL, TARGET_VAL, False)
simple_res_more_rel

Model    Type           Features    Parameters         RMSE  \
0  GBTRegressor  simple  more_rel_features  [20, 5, 0.1]  1962.177849   

       MAPE          MAE      Variance        R2  Adjusted_R2       Time  
0  0.065584  1449.905432  5.957271e+06  0.579387     0.579221  17.909714

In [19]:
utilities.show_results(simple_pred_more_rel, MODEL_NAME, TARGET_VAL)

In [20]:
# Valid performances with the corr matrix features
simple_res_less_rel, simple_pred_less_rel = utilities.evaluate_simple_model(df, less_rel_features, params, GDRIVE_LESS_REL_FEATURES_NAME, MODEL_NAME, FEATURES_LABEL, TARGET_VAL, False)
simple_res_less_rel

Model    Type           Features    Parameters         RMSE  \
0  GBTRegressor  simple  less_rel_features  [20, 5, 0.1]  6028.525663   

       MAPE          MAE      Variance        R2  Adjusted_R2       Time  
0  0.244022  4771.639722  3.517219e+07 -2.970346    -2.971908  15.381708

In [21]:
utilities.show_results(simple_pred_less_rel, MODEL_NAME, TARGET_VAL)

## Simple model (with data normalization)

In [22]:
# Valid performances with all the features
simple_norm_res_all, simple_norm_pred_all = utilities.evaluate_simple_model(df, all_features, params, GDRIVE_ALL_FEATURES_NAME, MODEL_NAME, FEATURES_LABEL, TARGET_VAL, True)
simple_norm_res_all

Model         Type      Features    Parameters         RMSE  \
0  GBTRegressor  simple_norm  all_features  [20, 5, 0.1]  9729.152764   

       MAPE         MAE      Variance        R2  Adjusted_R2       Time  
0  0.390468  8004.14912  9.682313e+07 -9.340847    -9.344918  16.162211

In [23]:
utilities.show_results(simple_norm_pred_all, MODEL_NAME, TARGET_VAL)

In [24]:
# Valid performances with the corr matrix features
simple_norm_res_more_rel, simple_norm_pred_more_rel = utilities.evaluate_simple_model(df, more_rel_features, params, GDRIVE_MORE_REL_FEATURES_NAME, MODEL_NAME, FEATURES_LABEL, TARGET_VAL, True)
simple_norm_res_more_rel

Model         Type           Features    Parameters        RMSE  \
0  GBTRegressor  simple_norm  more_rel_features  [20, 5, 0.1]  2046.79236   

       MAPE          MAE      Variance        R2  Adjusted_R2      Time  
0  0.068112  1495.105204  6.735215e+06  0.542329     0.542149  15.26736

In [25]:
utilities.show_results(simple_norm_pred_more_rel, MODEL_NAME, TARGET_VAL)

In [26]:
# Valid performances with the corr matrix features
simple_norm_res_less_rel, simple_norm_pred_less_rel = utilities.evaluate_simple_model(df, less_rel_features, params, GDRIVE_LESS_REL_FEATURES_NAME, MODEL_NAME, FEATURES_LABEL, TARGET_VAL, True)
simple_norm_res_less_rel

Model         Type           Features    Parameters          RMSE  \
0  GBTRegressor  simple_norm  less_rel_features  [20, 5, 0.1]  14457.015818   

      MAPE           MAE      Variance         R2  Adjusted_R2       Time  
0  0.67776  13442.528128  2.037501e+08 -21.833022   -21.842009  15.037095

In [27]:
utilities.show_results(simple_norm_pred_less_rel, MODEL_NAME, TARGET_VAL)

## Hyperparameter tuning

In [28]:
choosen_features = all_features
CHOSEN_FEATURES_LABEL = GDRIVE_ALL_FEATURES_NAME

In [29]:
# Split proportion list
PORTION_LIST = [0.6, 0.7, 0.8, 0.9]

In [30]:
# Get simple params
params = parameters.get_model_params(MODEL_NAME)
params

{'maxIter': [10, 20, 30], 'maxDepth': [3, 5, 8], 'stepSize': [0.1, 0.5, 0.7]}

In [31]:
hyp_res, hyp_params = utilities.autoTuning(df, choosen_features, params, CHOSEN_FEATURES_LABEL, PORTION_LIST, MODEL_NAME, FEATURES_LABEL, TARGET_VAL)
hyp_res

Model        Type      Features  Proportion    Parameters  \
0  GBTRegressor  autotuning  all_features         0.9  [20, 3, 0.5]   

          RMSE      MAPE          MAE      Variance        R2  Adjusted_R2  \
0  3466.828124  0.155836  3014.335046  9.333072e+06 -0.313018    -0.313535   

       Time  
0  8.209601

## Cross validation

In [32]:
# Get tuned params
params = hyp_params
params

{'maxIter': [20], 'maxDepth': [3], 'stepSize': [0.5]}

In [33]:
## Cross Validation Parameter
# Multiple Splits Time Series Cross Validation
mul_cv = {'cv_type':'mulTs',
          'kSplits': 5}

# Blocked Time Series Cross Validation
blk_cv = {'cv_type':'blkTs',
          'kSplits': 10}

In [34]:
mul_cv_res, trained_models_mul_cv = utilities.tsCrossValidation(df, choosen_features, params, mul_cv, CHOSEN_FEATURES_LABEL, MODEL_NAME, FEATURES_LABEL, TARGET_VAL)
mul_cv_res

Model   Type      Features  Splits Train&Validation    Parameters  \
0  GBTRegressor  mulTs  all_features       1   (21181, 21181)  [20, 3, 0.5]   
1  GBTRegressor  mulTs  all_features       2   (42362, 21181)  [20, 3, 0.5]   
2  GBTRegressor  mulTs  all_features       3   (63543, 21181)  [20, 3, 0.5]   
3  GBTRegressor  mulTs  all_features       4   (84724, 21181)  [20, 3, 0.5]   
4  GBTRegressor  mulTs  all_features       5  (105905, 21181)  [20, 3, 0.5]   

           RMSE      MAPE           MAE      Variance        R2  Adjusted_R2  \
0   6610.865904  0.659590   5120.887635  2.621841e+07 -1.450198    -1.450776   
1   2435.097592  0.368719   1879.078008  3.540906e+05 -0.119096    -0.119361   
2   2423.200611  0.202114   1989.036757  4.411575e+06 -1.313697    -1.314244   
3  36103.560383  0.735559  33522.947160  1.127523e+09 -6.359528    -6.361265   
4  10502.246498  0.385988   8639.155020  1.727559e+08 -0.328158    -0.328471   

       Time  
0  7.587343  
1  6.821713  
2  6.608205  
3  8.748634  
4  9.430910

In [35]:
blk_cv_res, trained_models_mul_cv = utilities.tsCrossValidation(df, choosen_features, params, blk_cv, CHOSEN_FEATURES_LABEL, MODEL_NAME, FEATURES_LABEL, TARGET_VAL)
blk_cv_res

Model   Type      Features  Splits Train&Validation    Parameters  \
0  GBTRegressor  blkTs  all_features       1    (10166, 2542)  [20, 3, 0.5]   
1  GBTRegressor  blkTs  all_features       2    (10166, 2542)  [20, 3, 0.5]   
2  GBTRegressor  blkTs  all_features       3    (10166, 2542)  [20, 3, 0.5]   
3  GBTRegressor  blkTs  all_features       4    (10166, 2542)  [20, 3, 0.5]   
4  GBTRegressor  blkTs  all_features       5    (10166, 2542)  [20, 3, 0.5]   
5  GBTRegressor  blkTs  all_features       6    (10166, 2542)  [20, 3, 0.5]   
6  GBTRegressor  blkTs  all_features       7    (10166, 2542)  [20, 3, 0.5]   
7  GBTRegressor  blkTs  all_features       8    (10166, 2542)  [20, 3, 0.5]   
8  GBTRegressor  blkTs  all_features       9    (10166, 2542)  [20, 3, 0.5]   
9  GBTRegressor  blkTs  all_features      10    (10166, 2542)  [20, 3, 0.5]   

           RMSE      MAPE           MAE      Variance         R2  Adjusted_R2  \
0     64.425035  0.105316     61.454449  3.810047e+03 -10.322576   -10.344900   
1    852.954591  0.304074    684.733774  4.693515e+05  -1.691334    -1.696640   
2   4561.968933  0.412912   4359.957256  2.153609e+07  -7.400086    -7.416648   
3    703.377389  0.071400    359.942864  9.810298e+04  -0.308297    -0.310876   
4   1281.712072  0.092089   1043.165137  1.323750e+06  -1.445673    -1.450495   
5   1246.722069  0.163815   1088.693384  8.404860e+05  -0.671466    -0.674762   
6  12216.087071  0.321772  10279.398661  1.062188e+08  -2.067350    -2.073398   
7   9655.630649  0.175113   8627.947892  1.111410e+08  -2.178610    -2.184877   
8   9896.748345  0.380452   8258.392668  7.096195e+07  -3.601698    -3.610771   
9   2733.018535  0.084967   2174.545042  3.729395e+06  -0.317841    -0.320440   

       Time  
0  4.472205  
1  6.028167  
2  4.535246  
3  5.834363  
4  4.464534  
5  5.453547  
6  4.254927  
7  5.117181  
8  4.365410  
9  4.467323

## Comparison table

In [36]:
# Define what model_info and evaluators in the Model Comparison Table
model_info = ['Model','Type', 'Features', 'Parameters']
evaluator_lst = ['RMSE','MAPE','MAE','Variance','R2','Adjusted_R2','Time']

# The the Cross Validation results would like to compare
comparison_lst = [simple_res_all, simple_res_more_rel, simple_res_less_rel, simple_norm_res_all, simple_norm_res_more_rel, simple_norm_res_less_rel, hyp_res, mul_cv_res, blk_cv_res]

In [37]:
# Show the Comparison Table
pd.concat([utilities.modelComparison(cv_result, model_info, evaluator_lst) for cv_result in comparison_lst])

Model         Type           Features    Parameters          RMSE  \
0  GBTRegressor       simple       all_features  [20, 5, 0.1]   2143.429339   
0  GBTRegressor       simple  more_rel_features  [20, 5, 0.1]   1962.177849   
0  GBTRegressor       simple  less_rel_features  [20, 5, 0.1]   6028.525663   
0  GBTRegressor  simple_norm       all_features  [20, 5, 0.1]   9729.152764   
0  GBTRegressor  simple_norm  more_rel_features  [20, 5, 0.1]   2046.792360   
0  GBTRegressor  simple_norm  less_rel_features  [20, 5, 0.1]  14457.015818   
0  GBTRegressor   autotuning       all_features  [20, 3, 0.5]   3466.828124   
0  GBTRegressor        mulTs       all_features  [20, 3, 0.5]  11614.994198   
0  GBTRegressor        blkTs       all_features  [20, 3, 0.5]   4321.264469   

       MAPE           MAE      Variance         R2  Adjusted_R2       Time  
0  0.067424   1516.468454  5.544397e+06   0.498092     0.497894  29.956248  
0  0.065584   1449.905432  5.957271e+06   0.579387     0.579221  17.909714  
0  0.244022   4771.639722  3.517219e+07  -2.970346    -2.971908  15.381708  
0  0.390468   8004.149120  9.682313e+07  -9.340847    -9.344918  16.162211  
0  0.068112   1495.105204  6.735215e+06   0.542329     0.542149  15.267360  
0  0.677760  13442.528128  2.037501e+08 -21.833022   -21.842009  15.037095  
0  0.155836   3014.335046  9.333072e+06  -0.313018    -0.313535   8.209601  
0  0.470394  10230.220916  2.662526e+08  -1.914135    -1.914823   7.839361  
0  0.211191   3693.823113  3.163228e+07  -3.000493    -3.008381   4.899290

## Training the final model

In [38]:
model = utilities.train_final_model(df, choosen_features, params, MODEL_NAME, FEATURES_LABEL, TARGET_VAL)

In [39]:
GDRIVE_MODELS_DIR = GDRIVE_DIR + "/MyDrive/BDC/project/models"
GDRIVE_MODEL_NAME_EXT = GDRIVE_MODELS_DIR + "/" + MODEL_NAME

In [40]:
# Save the trained model
model.write().overwrite().save(GDRIVE_MODEL_NAME_EXT)